# 05 Tekstide puhastamine, sõnestamine, lemmatiseerimine

In [1]:
import pandas as pd
data = pd.read_excel('toofailid/DATA_TEKSTIKOGU_1ver1.xlsx', engine='openpyxl')
print(data.shape)

(636, 47)


In [2]:
sagedused = data['Lahendi liik'].value_counts()

In [3]:
sagedused

õigeksmõistev    350
tauniv           286
Name: Lahendi liik, dtype: int64

In [4]:
# Andmestiku segamine
#from sklearn.utils import shuffle
#data = shuffle(data)
#data = data.reset_index(drop=True)

In [5]:
# Ebavajaliku info  (aeg, pealkiri) eemaldamine
#data.drop(["date"],axis=1,inplace=True)
#data.drop(["title"],axis=1,inplace=True)
#data.drop(["subject"],axis=1,inplace=True)
#data.drop(["link"],axis=1,inplace=True)

In [6]:
tekst_list = data['text'].to_list()

In [7]:
# Funktsioon sümbolite eemaldamiseks
def remove_newlines_tabs(text):
    Formatted_text = text.replace('\n', '').replace('\n\n', '').replace(u'\xa0', '').replace(u'\xad', '').replace(u'\x96', '').replace('_x000d_', '').replace(u'\x9e', '').replace(u'\x93', '').replace(u'\x94', '')
    return Formatted_text

# Funktsioon html-vormingute eemaldamiseks
def strip_html_tags(text):
    soup = BeautifulSoup(text, "html.parser")
    # Get all the text other than html tags.
    stripped_text = soup.get_text(separator=" ")
    return stripped_text

# Funktsioon liigsete tühikute eemaldamiseks
def remove_whitespace(text):
    pattern = re.compile(r'\s+') 
    without_whitespace = re.sub(pattern, ' ', text)
    return without_whitespace

In [8]:
from bs4 import BeautifulSoup
import re
tekst_puhas = []
for tekst in tekst_list:
    s = strip_html_tags(tekst)    
    s = remove_newlines_tabs(s)
    s = remove_whitespace(s)
    tekst_puhas.append(s)

In [9]:
data['text_puhas'] = tekst_puhas

Teksti sõnestamine kasutades eesti keele sõnestusvahendeid. Seega loome meetodi, mis saab sisendiks sõne, sõnestab selle EstNLTK abil ning tagastab sõnade järjendi. 

In [10]:
from estnltk import Text

# Meetodid teksti sõnestamiseks estnltk abil
def tokenize_with_estnltk( input_string ):
    return Text(input_string).tag_layer(['words']).words.text

def lemmatize_with_estnltk(input_string):
    lemmad = Text(input_string).tag_layer(['morph_analysis']).lemma
    flattened = []
    for sublist in lemmad:
        flattened.append(sublist[0]) #valib esimese lemma
    return flattened

In [11]:
# Kirjavahemärkide eemaldamine
import string

def punctuation_removal(text):
    result = string.punctuation
    all_list = [char for char in text if char  not in string.punctuation]
    clean_str = ' '.join(all_list)
    return clean_str

In [12]:
tekst_tokenize = []

for tekst in tekst_puhas:
    s = tokenize_with_estnltk(tekst.lower())
    s = punctuation_removal(s)
    s = s.strip(".")
    s = s.replace('“', '').replace('„', '').replace('”', '').replace('–', '').replace('...', '').replace('«', '').replace('»', '').replace('…', '')
    tekst_tokenize.append(s)

In [13]:
len(tekst_tokenize)

636

In [14]:
tekst_lemmatize = []
for tekst in tekst_puhas:
    s = lemmatize_with_estnltk(tekst.lower())
    s = punctuation_removal(s)
    s = s.strip(".")
    s = s.replace('“', '').replace('„', '').replace('”', '').replace('–', '').replace('...', '').replace('«', '').replace('»', '').replace('…', '')
    tekst_lemmatize.append(s)

In [15]:
len(tekst_lemmatize)

636

In [16]:
tekst_lemmatize

['viimane päev valitsema külmalaine olema rivi välja lööma ühistranspordisõiduk kuid häda olema jääma autoomanik kes liiklusvahend madal külmakraad tõttu ei käivituma pärnu postimees võtma ühendus lehelugeja kes sõnutsi ei sõitma eile ega täna hommik tammine liin number 16 buss väidetavalt tooma dispetšer põhjus külmakraad  mina pidama hommik töö jõudma ja transpordifirma pidama see tagama  märkima pahane lugeja kes hinnang ei olema käre pakane vabandus  eile ja täna hommik olema külm tõesti palju linnaliinibuss liiklus häirima  tunnistama mtü pärnumaa ühistranspordikeskus pütk vanemlogistik tooma talts tema tooma välja et kuigi pärnu maakonnaliin ja liin number 40 olema buss sõitma probleem ei olema teine liin nii hästi läinud näiteks eile hommik jääma as sebe dispetšer andmed liin number 8 sõitma mõlema ring samuti liin number 3 kaks hommikune ring täna hommik esinema mitu buss käivitusprobleem  järgmine päev suhtes olema siiski optimistlikum ja loodetavasti suur liinihäire enam ei e

In [17]:
data['text_token'] = tekst_tokenize

In [18]:
data['text_lemmatize'] = tekst_lemmatize

In [19]:
data

#  \
0    1081   
1    1080   
2    1079   
3    1078   
4    1076   
..    ...   
631    13   
632     8   
633     6   
634     3   
635     2   

                                                                                                                title  \
0                                       Käre pakane viis bussid rivist välja, autoabi osutajatel käed-jalad tööd täis   
1    Miks räägib Varro Vooglaid üha enam relva haaramisest ja kodusõjast? "Näen väga suurt valu, ängi ja kibestumist"   
2                                                            Maksumaksjale läks Valge Ingli afäär maksma 51 000 eurot   
3                                                                             Jalutuskäik Tiit Leito elutöö varemetel   
4                     Parkett kummis, tuul puhub läbi. Ostja esitas kümnete ehitusvigade tõttu arendaja vastu kaebuse   
..                                                                                                                ...   
631                                                                                                    Iseseisvuspäev   
632                                                                  Järvi fondi juhid jagasid raha enda projektidele   
633                                                                     Päevaintervjuu: Selja hakkab uut sängi otsima   
634                                                                     Ettevõtted hoiavad võõra vöötkoodi abil kokku   
635                                                                      Juustutootjad keelduvad koostööst Estoveriga   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

## Tunnuste lisamine

In [20]:
# Eesti ajakirjanduseetika koodeksi punktid
koodeksipunktid = ['1.2', '1.5', '1.6', 
                   '2.3', 
                   '3.1','3.2', '3.3', '3.5', '3.6','3.7',
                   '4.2', '4.3', '4.4', '4.6', '4.7', '4.8', '4.9', '4.10', '4.12',
                   '5.1', '5.2', '5.3',
                   '6.1']

data['k_muu'] = data[koodeksipunktid].sum(axis=1)

In [21]:
labels = data['Lahendi liik'].to_list()
k1_4 = data['1.4'].to_list()
k4_1 = data['4.1'].to_list()
k4_11 = data['4.11'].to_list()
k_muu = data['k_muu'].to_list()
del data['k_muu']

In [22]:
len(k_muu)

636

In [23]:
ÕM = []
T1_4 = []
T4_1 = []
T4_11 = []
T_muu = []

for i, value in enumerate(labels):
    if value == 'õigeksmõistev':
        ÕM.append(1)
        T1_4.append(0)
        T4_1.append(0)
        T4_11.append(0)
        T_muu.append(0)
    else:
        ÕM.append(0)
        T1_4.append(k1_4[i])
        T4_1.append(k4_1[i])
        T4_11.append(k4_11[i])
        T_muu.append(k_muu[i])

In [24]:
data['T1_4'] = T1_4
data['T4_1'] = T4_1
data['T4_11'] = T4_11
data['T_muu'] = T_muu
data['ÕM'] = ÕM

In [25]:
data

#  \
0    1081   
1    1080   
2    1079   
3    1078   
4    1076   
..    ...   
631    13   
632     8   
633     6   
634     3   
635     2   

                                                                                                                title  \
0                                       Käre pakane viis bussid rivist välja, autoabi osutajatel käed-jalad tööd täis   
1    Miks räägib Varro Vooglaid üha enam relva haaramisest ja kodusõjast? "Näen väga suurt valu, ängi ja kibestumist"   
2                                                            Maksumaksjale läks Valge Ingli afäär maksma 51 000 eurot   
3                                                                             Jalutuskäik Tiit Leito elutöö varemetel   
4                     Parkett kummis, tuul puhub läbi. Ostja esitas kümnete ehitusvigade tõttu arendaja vastu kaebuse   
..                                                                                                                ...   
631                                                                                                    Iseseisvuspäev   
632                                                                  Järvi fondi juhid jagasid raha enda projektidele   
633                                                                     Päevaintervjuu: Selja hakkab uut sängi otsima   
634                                                                     Ettevõtted hoiavad võõra vöötkoodi abil kokku   
635                                                                      Juustutootjad keelduvad koostööst Estoveriga   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [26]:
data.to_csv('toofailid/DATA_TEKSTIKOGU_puhastatud.csv',index=False)
read_file = pd.read_csv (r'toofailid/DATA_TEKSTIKOGU_puhastatud.csv')
read_file.to_excel (r'toofailid/DATA_TEKSTIKOGU_puhastatud.xlsx', index = None, header=True)